In [155]:
import re
import numpy as np
import pandas as pd

from sklearn.linear_model import SGDClassifier
from sklearn.svm import SVC, LinearSVC
from sklearn.linear_model import LogisticRegression

from sklearn.metrics import accuracy_score, roc_auc_score
from sklearn.model_selection import cross_val_score, GridSearchCV, ShuffleSplit

from sklearn.preprocessing import normalize

%matplotlib inline

# Import Data

In [156]:
folder = "~/workspace/datasets/ml-mipt-spring2018-hw5-v1/"
data = pd.read_csv(folder + 'train.csv')
data.drop('id', axis = 1, inplace = True)
X_train = np.asarray(data[data.columns[range(1, data.shape[1])]], dtype = np.double)
Y_train = np.asarray(data[['label']], dtype = np.double).ravel()
data.head()

label  feat1  feat2  feat3  feat4  feat5  feat6  feat7  feat8  feat9  \
0      1      7      0      3      0      2      3      0      6      0   
1      1      0     11      0      0     10      1      0      0      4   
2      0      9      0      3      0      1      3      0      4      0   
3      0      0      9      3      2     25      0      4      0      0   
4      0      0      0      0      0      2      5      0      0      0   

    ...     feat207  feat208  feat209  feat210  feat211  feat212  feat213  \
0   ...           3        4        2        2        0       13        0   
1   ...           0        2        0        0        2        8        1   
2   ...          48       11        2        0        0        4        0   
3   ...           1       14        1        0        0        0        3   
4   ...           3       12        0        3        0        4        0   

   feat214  feat215  feat216  
0       11        1        3  
1       13        0        4  
2        2        0        0  
3        0       17        1  
4       24        4        0  

[5 rows x 217 columns]

In [157]:
data.groupby(['label']).count()

feat1  feat2  feat3  feat4  feat5  feat6  feat7  feat8  feat9  feat10  \
label                                                                          
0        327    327    327    327    327    327    327    327    327     327   
1        573    573    573    573    573    573    573    573    573     573   

        ...     feat207  feat208  feat209  feat210  feat211  feat212  feat213  \
label   ...                                                                     
0       ...         327      327      327      327      327      327      327   
1       ...         573      573      573      573      573      573      573   

       feat214  feat215  feat216  
label                             
0          327      327      327  
1          573      573      573  

[2 rows x 216 columns]

# Feature transformation

In [158]:
def transform_id(X, X_train):
    return X

In [159]:
def transform_normed(X, X_train):
    return (X - X_train.mean(axis=0)) / X_train.std(axis=0)

In [160]:
def transform_scaled(X, X_train):
    return X / X_train.max(axis=0)

# Fit Methods

In [161]:
transformations = [
    transform_id, transform_normed, transform_scaled
]

In [209]:
estimators = [
    SGDClassifier(max_iter=50000, tol=0.1, penalty='l1', alpha=0.1),
    SGDClassifier(max_iter=50000, tol=0.1, penalty='l2', alpha=0.1),
    SVC(kernel='rbf', C = 0.1, gamma=2),
    SVC(kernel='linear', C = 0.1, gamma=2),
    SVC(kernel='sigmoid', C = 0.1, gamma=2),
    SVC(kernel='poly', C = 0.1, gamma=2),
    
    SVC(kernel='rbf', C = 1, gamma=2),
    SVC(kernel='linear', C = 1, gamma=2),
    SVC(kernel='sigmoid', C = 1, gamma=2),
    SVC(kernel='poly', C = 1, gamma=2),
    
    SVC(kernel='rbf', C = 0.1, gamma="auto"),
    SVC(kernel='linear', C = 0.1, gamma="auto"),
    SVC(kernel='sigmoid', C = 0.1, gamma="auto"),
    SVC(kernel='poly', C = 0.1, gamma="auto"),
    
    SVC(kernel='rbf', C = 1, gamma="auto"),
    SVC(kernel='linear', C = 1, gamma="auto"),
    SVC(kernel='sigmoid', C = 1, gamma="auto"),
    SVC(kernel='poly', C = 11, gamma="auto"),
    
    #SVC(kernel='precomputed', C = 0.1, gamma=2),
    #LinearSVC(penalty = 'l1', loss='hinge'), 
    LinearSVC(penalty = 'l1', loss='squared_hinge', dual=False),
    LinearSVC(penalty = 'l2', loss='hinge'),
    LinearSVC(penalty = 'l2', loss='squared_hinge', dual=False),# 'hinge' or 'squared_hinge', 
    LogisticRegression(penalty='l1', C=0.2),
    LogisticRegression(penalty='l1', C=1),
    LogisticRegression(penalty='l2', C=0.2),
    LogisticRegression(penalty='l2', C=1),
]

In [210]:
grid_result = []
cv_strategy = ShuffleSplit(n_splits=10, test_size=0.2, random_state=33)
for transform_i, transform in enumerate(transformations):
    X_train_transformed = transform(X_train, X_train)
    transform_name = str(transform).split(" ")[1]
    for estimator_i, estimator in enumerate(estimators):
        %time scoring = cross_val_score(estimator, X_train_transformed, Y_train, scoring='roc_auc', cv=cv_strategy)
        estimator_name_short = str(estimator)
        score_mean = scoring.mean()
        score_std = scoring.std()
        grid_result.append((transform_i, estimator_i, score_mean, score_std))
        print ('{}\n #data = {}, mean = {}, std = {}\n'.format(
            estimator_name_short, transform_name, round(score_mean, 4), round(score_std, 4)))

CPU times: user 2.08 s, sys: 3.65 s, total: 5.74 s
Wall time: 892 ms
SGDClassifier(alpha=0.1, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=True, l1_ratio=0.15,
       learning_rate='optimal', loss='hinge', max_iter=50000, n_iter=None,
       n_jobs=1, penalty='l1', power_t=0.5, random_state=None,
       shuffle=True, tol=0.1, verbose=0, warm_start=False)
 #data = transform_id, mean = 0.852, std = 0.0523

CPU times: user 188 ms, sys: 379 ms, total: 567 ms
Wall time: 72.4 ms
SGDClassifier(alpha=0.1, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=True, l1_ratio=0.15,
       learning_rate='optimal', loss='hinge', max_iter=50000, n_iter=None,
       n_jobs=1, penalty='l2', power_t=0.5, random_state=None,
       shuffle=True, tol=0.1, verbose=0, warm_start=False)
 #data = transform_id, mean = 0.9045, std = 0.0258

CPU times: user 1.7 s, sys: 475 ms, total: 2.17 s
Wall time: 1.55 s
SVC(C=0.1, cache_size=200, class_weight=None, co

CPU times: user 2.68 s, sys: 4.91 s, total: 7.59 s
Wall time: 1.05 s
LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)
 #data = transform_id, mean = 0.9191, std = 0.0152

CPU times: user 292 ms, sys: 472 ms, total: 764 ms
Wall time: 96 ms
SGDClassifier(alpha=0.1, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=True, l1_ratio=0.15,
       learning_rate='optimal', loss='hinge', max_iter=50000, n_iter=None,
       n_jobs=1, penalty='l1', power_t=0.5, random_state=None,
       shuffle=True, tol=0.1, verbose=0, warm_start=False)
 #data = transform_normed, mean = 0.8203, std = 0.0466

CPU times: user 158 ms, sys: 270 ms, total: 428 ms
Wall time: 55 ms
SGDClassifier(alpha=0.1, average=False, class_weight=None, epsilon=0.1,
       eta0=0.0, fit_intercept=

CPU times: user 2.77 s, sys: 4.7 s, total: 7.47 s
Wall time: 1.18 s
LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l1', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)
 #data = transform_normed, mean = 0.921, std = 0.0207

CPU times: user 1.37 s, sys: 2.41 s, total: 3.79 s
Wall time: 520 ms
LogisticRegression(C=0.2, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)
 #data = transform_normed, mean = 0.9262, std = 0.0195

CPU times: user 1.8 s, sys: 3.48 s, total: 5.28 s
Wall time: 698 ms
LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
       

CPU times: user 658 ms, sys: 1.27 s, total: 1.93 s
Wall time: 247 ms
LinearSVC(C=1.0, class_weight=None, dual=False, fit_intercept=True,
     intercept_scaling=1, loss='squared_hinge', max_iter=1000,
     multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
     verbose=0)
 #data = transform_scaled, mean = 0.9253, std = 0.0176

CPU times: user 309 ms, sys: 588 ms, total: 897 ms
Wall time: 113 ms
LogisticRegression(C=0.2, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l1', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)
 #data = transform_scaled, mean = 0.9005, std = 0.0197

CPU times: user 521 ms, sys: 1.1 s, total: 1.62 s
Wall time: 208 ms
LogisticRegression(C=1, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l1', random_state=None, solver='l

In [211]:
grid_result = np.array(grid_result)
best_5 = grid_result[:, 2].argsort()[-5:][::-1]
for i in best_5:
    print(grid_result[i])
    transformation = transformations[int(grid_result[i, 0])]
    transform_name = str(transform).split(" ")[1]
    estimator_name = str(estimators[int(grid_result[i, 1])])
    score_mean =  grid_result[i, 2]
    score_std =  grid_result[i, 3]
    print ('{}\n #data = {}, mean = {}, std = {}\n'.format(
        estimator_name, transform_name, round(score_mean, 4), round(score_std, 4)))

[2.         2.         0.97509331 0.00897977]
SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=2, kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)
 #data = transform_scaled, mean = 0.9751, std = 0.009

[2.         6.         0.97485828 0.00721492]
SVC(C=1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=2, kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)
 #data = transform_scaled, mean = 0.9749, std = 0.0072

[0.00000000e+00 1.00000000e+01 9.67616369e-01 9.26588469e-03]
SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)
 #data = transform_scaled, mean = 0.9676, std = 0.0093

[0.00000000e+00 

# Get final classifier

In [218]:
best_i = int(grid_result[:, 2].argmax())
print(grid_result[best_i])
transformation = transformations[int(grid_result[best_i, 0])]
estimator = estimators[int(grid_result[best_i, 1])]
print("Best:", transformation, estimator)
X_train_transformed = transformation(X_train, X_train)
estimator.fit(X_train_transformed, Y_train)

[2.         2.         0.97509331 0.00897977]
Best: <function transform_scaled at 0x7fce076ca7b8> SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=2, kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)


SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=2, kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)

# Some parameters fitting

In [168]:
params = {
    "C":np.linspace(0.01, 100, 20),
    "gamma":np.linspace(0.01, 100, 20),
    "degree":np.arange(1, 10)
}
gscv = GridSearchCV(estimator, params, scoring='roc_auc', n_jobs=-1, verbose=100, cv=Str)
gscv.fit(X_train_transformed, Y_train)

Fitting 3 folds for each of 3600 candidates, totalling 10800 fits
[CV] C=0.01, degree=1, gamma=0.01 ....................................
[CV] C=0.01, degree=1, gamma=0.01 ....................................
[CV] C=0.01, degree=1, gamma=0.01 ....................................
[CV] C=0.01, degree=1, gamma=5.272631578947368 .......................
[CV] C=0.01, degree=1, gamma=5.272631578947368 .......................
[CV] C=0.01, degree=1, gamma=5.272631578947368 .......................
[CV] C=0.01, degree=1, gamma=10.535263157894736 ......................
[CV] C=0.01, degree=1, gamma=10.535263157894736 ......................
Memmaping (shape=(900, 216), dtype=float64) to new file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm

[CV] C=0.01, degree=1, gamma=26.32315789473684 .......................
[Parallel(n_jobs=-1)]: Done   8 tasks      | elapsed:    0.6s
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
[CV]  C=0.01, degree=1, gamma=10.535263157894736, score=0.9566501753206206, total=   0.3s
[CV]  C=0.01, degree=1, gamma=15.797894736842105, score=0.921658100773332, total=   0.3s
[CV] C=0.01, degree=1, gamma=26.32315789473684 .......................
[CV] C=0.01, degree=1, gamma=26.32315789473684 .......................
[CV]  C=0.01, degree=1, gamma=15.797894736842105, score=0.926629521110524, total=   0.3s
[CV]  C=0.01, degree=1, gamma=15.797894736842105, score=0.9453864258609923, total=   0.3s
[CV] C=0.01, degree=1, gamma=31.585789473684212 .................

[CV]  C=0.01, degree=1, gamma=42.11105263157894, score=0.8565252893991067, total=   0.3s
[CV] C=0.01, degree=1, gamma=57.89894736842105 .......................
[CV]  C=0.01, degree=1, gamma=47.373684210526314, score=0.8400499543686056, total=   0.3s
[CV] C=0.01, degree=1, gamma=57.89894736842105 .......................
[CV]  C=0.01, degree=1, gamma=42.11105263157894, score=0.8695422450646044, total=   0.3s
[CV] C=0.01, degree=1, gamma=57.89894736842105 .......................
[CV]  C=0.01, degree=1, gamma=47.373684210526314, score=0.8565252893991067, total=   0.3s
[CV] C=0.01, degree=1, gamma=63.16157894736842 .......................
[Parallel(n_jobs=-1)]: Done  26 tasks      | elapsed:    1.9s
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=in

[CV]  C=0.01, degree=1, gamma=73.68684210526315, score=0.8565252893991067, total=   0.5s
[CV] C=0.01, degree=1, gamma=89.47473684210526 .......................
[CV]  C=0.01, degree=1, gamma=78.94947368421053, score=0.8373841202747491, total=   0.4s
[CV] C=0.01, degree=1, gamma=89.47473684210526 .......................
[CV]  C=0.01, degree=1, gamma=84.2121052631579, score=0.8565252893991067, total=   0.3s
[CV]  C=0.01, degree=1, gamma=84.2121052631579, score=0.8373841202747491, total=   0.3s
[CV] C=0.01, degree=1, gamma=94.73736842105264 .......................
[CV]  C=0.01, degree=1, gamma=78.94947368421053, score=0.8565252893991067, total=   0.3s
[CV] C=0.01, degree=1, gamma=94.73736842105264 .......................
[Parallel(n_jobs=-1)]: Done  45 tasks      | elapsed:    3.1s
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64

[CV]  C=0.01, degree=2, gamma=0.01, score=0.9145011768096449, total=   0.3s
[CV] C=0.01, degree=2, gamma=10.535263157894736 ......................
[CV]  C=0.01, degree=2, gamma=0.01, score=0.8376002689850617, total=   0.3s
[CV] C=0.01, degree=2, gamma=15.797894736842105 ......................
[CV]  C=0.01, degree=2, gamma=0.01, score=0.9106585330707526, total=   0.3s
[CV] C=0.01, degree=2, gamma=15.797894736842105 ......................
[Parallel(n_jobs=-1)]: Done  61 tasks      | elapsed:    3.9s
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
[Parallel(n_jobs=-1)]: Done  62 tasks      | elapsed:    4.1s
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d

...

[CV]  C=100.0, degree=8, gamma=100.0, score=0.8695422450646044, total=   0.3s
[CV] C=100.0, degree=9, gamma=15.797894736842105 .....................
[CV]  C=100.0, degree=9, gamma=5.272631578947368, score=0.956818290984197, total=   0.3s
[CV] C=100.0, degree=9, gamma=15.797894736842105 .....................
[CV]  C=100.0, degree=9, gamma=5.272631578947368, score=0.9529276141985686, total=   0.3s
[CV] C=100.0, degree=9, gamma=21.060526315789474 .....................
[CV]  C=100.0, degree=9, gamma=5.272631578947368, score=0.9583073154330178, total=   0.3s
[CV] C=100.0, degree=9, gamma=21.060526315789474 .....................
[CV]  C=100.0, degree=9, gamma=15.797894736842105, score=0.9403909890004323, total=   0.2s
[CV]  C=100.0, degree=9, gamma=10.535263157894736, score=0.9455305250012008, total=   0.3s
[CV]  C=100.0, degree=9, gamma=10.535263157894736, score=0.9545607377875979, total=   0.3s
[CV] C=100.0, degree=9, gamma=21.060526315789474 .....................
[Parallel(n_jobs=-1)]: Do

[Parallel(n_jobs=-1)]: Done 10758 tasks      | elapsed:  9.5min
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
[Parallel(n_jobs=-1)]: Done 10759 tasks      | elapsed:  9.5min
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
[CV]  C=100.0, degree=9, gamma=31.585789473684212, score=0.867212642297901, total=   0.3s
[CV] C=100.0, degree=9, gamma=47.373684210526314 .....................
[CV]  C=100.0, degree=9, gamma=31.585789473684212, score=0.8819828041692684, total=   0.3s
[CV] C=100.0, de

[CV] C=100.0, degree=9, gamma=68.42421052631579 ......................
[CV]  C=100.0, degree=9, gamma=57.89894736842105, score=0.8565252893991067, total=   0.3s
[CV] C=100.0, degree=9, gamma=73.68684210526315 ......................
[CV]  C=100.0, degree=9, gamma=57.89894736842105, score=0.8695422450646044, total=   0.3s
[CV] C=100.0, degree=9, gamma=73.68684210526315 ......................
[CV]  C=100.0, degree=9, gamma=63.16157894736842, score=0.8373841202747491, total=   0.2s
[CV] C=100.0, degree=9, gamma=73.68684210526315 ......................
[Parallel(n_jobs=-1)]: Done 10774 tasks      | elapsed:  9.5min
Memmaping (shape=(900, 216), dtype=float64) to old file /dev/shm/joblib_memmaping_pool_30709_140522860873040/30709-140522864589176-6d409366264fa0e41302210bd278b312.pkl
Pickling array (shape=(900,), dtype=float64).
Pickling array (shape=(600,), dtype=int64).
Pickling array (shape=(300,), dtype=int64).
[Parallel(n_jobs=-1)]: Done 10775 tasks      | elapsed:  9.5min
Memmaping (shape

[CV]  C=100.0, degree=9, gamma=94.73736842105264, score=0.8695422450646044, total=   0.3s
[CV]  C=100.0, degree=9, gamma=94.73736842105264, score=0.837384120274749, total=   0.3s
[CV]  C=100.0, degree=9, gamma=100.0, score=0.837384120274749, total=   0.3s
[CV]  C=100.0, degree=9, gamma=100.0, score=0.8565252893991067, total=   0.2s
[CV]  C=100.0, degree=9, gamma=100.0, score=0.8695422450646044, total=   0.2s
[Parallel(n_jobs=-1)]: Done 10800 out of 10800 | elapsed:  9.6min finished


GridSearchCV(cv=None, error_score='raise',
       estimator=SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=2, kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'C': array([1.00000e-02, 5.27263e+00, 1.05353e+01, 1.57979e+01, 2.10605e+01,
       2.63232e+01, 3.15858e+01, 3.68484e+01, 4.21111e+01, 4.73737e+01,
       5.26363e+01, 5.78989e+01, 6.31616e+01, 6.84242e+01, 7.36868e+01,
       7.89495e+01, 8.42121e+01, 8.94747e+01, 9.47374e+01, 1.00000e... 8.42121e+01, 8.94747e+01, 9.47374e+01, 1.00000e+02]), 'degree': array([1, 2, 3, 4, 5, 6, 7, 8, 9])},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=100)

In [169]:
gscv.best_score_

0.9572505884048226

In [170]:
gscv.best_params_

{'C': 0.01, 'degree': 1, 'gamma': 5.272631578947368}

# Finally get the best estimator

In [236]:
estimator = SVC(kernel='poly', C = 0.1, gamma=2),
estimator

SVC(C=0.01, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma=5.272631578947368,
  kernel='poly', max_iter=-1, probability=False, random_state=None,
  shrinking=True, tol=0.001, verbose=False)

In [237]:
Y_train

array([1., 1., 0., 0., 0., 1., 0., 1., 0., 0., 1., 1., 0., 1., 1., 1., 1.,
       0., 1., 1., 0., 1., 0., 1., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1.,
       1., 0., 1., 1., 1., 1., 0., 1., 1., 0., 1., 1., 1., 1., 0., 1., 0.,
       1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 1., 1., 1., 0., 1., 1., 0.,
       0., 0., 1., 1., 1., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1., 0.,
       0., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 0., 0., 1., 0., 0., 1., 1., 1., 1., 0., 0.,
       1., 1., 0., 0., 0., 0., 1., 0., 1., 1., 1., 0., 0., 1., 0., 0., 0.,
       0., 1., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 1., 1., 1., 1., 1.,
       0., 1., 1., 0., 1., 1., 1., 0., 1., 1., 1., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 0.,
       1., 0., 1., 1., 0., 1., 0., 0., 0., 1., 0., 1., 0., 1., 1., 1., 1.,
       1., 1., 1., 1., 0., 1., 0., 1., 1., 0., 0., 1., 0., 0., 1., 0., 1.,
       0., 1., 1., 0., 0.

In [238]:
estimator.fit(X_train_transformed, Y_train)
estimator.predict(X_train_transformed)

array([1., 1., 0., 0., 0., 1., 0., 1., 0., 0., 1., 1., 0., 1., 1., 1., 1.,
       0., 1., 1., 0., 1., 0., 1., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1.,
       1., 0., 1., 1., 1., 1., 0., 1., 1., 0., 1., 1., 1., 1., 0., 1., 0.,
       1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 1., 1., 1., 0., 1., 1., 0.,
       0., 0., 1., 1., 1., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1., 0.,
       0., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 0., 0., 1., 0., 0., 1., 1., 1., 1., 0., 0.,
       1., 1., 0., 0., 0., 0., 1., 0., 1., 1., 1., 0., 0., 1., 0., 0., 0.,
       0., 1., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 1., 1., 1., 1., 1.,
       0., 1., 1., 0., 1., 1., 1., 0., 1., 1., 1., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 0.,
       1., 0., 1., 1., 0., 1., 0., 0., 0., 1., 0., 1., 0., 1., 1., 1., 1.,
       1., 1., 1., 1., 0., 1., 0., 1., 1., 0., 0., 1., 0., 0., 1., 0., 1.,
       0., 1., 1., 0., 0.

# Test data estimation

In [229]:
test = pd.read_csv(folder + 'test.csv')
X_test = np.asarray(test[test.columns[range(1, test.shape[1])]])
X_test = transformation(X_test, X_train)
X_test

array([[0.22222222, 0.03508772, 0.05263158, ..., 0.07594937, 0.06451613,
        0.05882353],
       [0.16666667, 0.05263158, 0.        , ..., 0.34177215, 0.06451613,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.06329114, 0.03225806,
        0.01960784],
       ...,
       [0.05555556, 0.01754386, 0.        , ..., 0.4556962 , 0.        ,
        0.03921569],
       [0.05555556, 0.05263158, 0.05263158, ..., 0.44303797, 0.03225806,
        0.        ],
       [0.        , 0.03508772, 0.07894737, ..., 0.18987342, 0.        ,
        0.        ]])

In [230]:
test_predict=estimator.predict(X_test)
test['label'] = test_predict
test[['id', 'label']].to_csv('sol_1.csv', sep = ',', index = False)
test

id  feat1  feat2  feat3  feat4  feat5  feat6  feat7  feat8  feat9  \
0        1      4      2      2      0      4      2      1      2      1   
1        2      3      3      0      0      1      2      0      9      3   
2        3      0      0      0      2      2      8      0      1      0   
3        4      0      0      0      0      0      0      0      7      0   
4        5      1      2      3      0      2      0      0     13      0   
5        6      0     13      0      0      2      0      0      4      5   
6        7      0      3      1      4      0      0      0      3      2   
7        8      0      7      1      0      1      2      0     19      5   
8        9     10      0      1      0      0      0      2      6      1   
9       10      2      0      2      0      2      4      1      2      0   
10      11      0      1      0      0      0      0      0      2      1   
11      12      0      0      0      0      0     24      0     29      0   
12      13     11      1      2      3      1      2      6      1      1   
13      14      8      1      8      2      2      3      6      5      0   
14      15     12      0      1      0      1      0      2      0      0   
15      16     10      0      0      0      1      1      4      4      0   
16      17      0      5      0      1      1      1      0     12      3   
17      18      0     15      1      1      3      2      0      5      0   
18      19      1      5      0      1      0      0      0      1      5   
19      20      4      2      1      0      3      0      1     13      5   
20      21      2      1      3      0      0      0      1      3      1   
21      22      8      0      0      2      0      2      3      1      0   
22      23      2      1      0      0      4     10      0      6      1   
23      24      2      5      2      0      1     11      5      3      0   
24      25      6      3      3      2      0      4      2      8      2   
25      26      0      0      0      0      5      1      0      3      0   
26      27      0      6      4      0      0      0      0      4      7   
27      28      0     32      1      0      4      0      1      0      9   
28      29      0      5      3      1      0      1      1     11      5   
29      30      2      3      1      0      0      3      2      4      4   
...    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
9020  9021      1      1      0      0      0      2      0      5      0   
9021  9022      3      0      0      0      0      5      0      5      0   
9022  9023      3      0      0      3      5     18      0      3      0   
9023  9024      9      0      5      0      0      2      5      0      0   
9024  9025      0      0      5      0      7     14      0      3      0   
9025  9026      1      1      1      1      0      2      0      4      0   
9026  9027      1      0      0      0      9      2      1      0      0   
9027  9028      0      1      3      0      0      1      1      9      2   
9028  9029      5      0      9      3      0      4      0      4      1   
9029  9030      0      0     24      1      0      0     10      0      1   
9030  9031      2      1      2      1      7      3      8      1      0   
9031  9032      0      0      1      1      0      6      0     13      0   
9032  9033      1      4      0      0      6      2      0     11      0   
9033  9034      3      0      8      1      0     19      2      1      0   
9034  9035      9      1      3      1      2      5      4      1      0   
9035  9036      0      4      1      0     37      4      0      0      1   
9036  9037      0      4      2      0      0      2      0     17      3   
9037  9038      2      4      3      0      0      0      7      5      2   
9038  9039      1      5      2      1      4      2      0      3      1   
9039  9040      1      9      2      1      3      5      3      5      1   
9040

In [232]:
estimator, transformation

(SVC(C=0.1, cache_size=200, class_weight=None, coef0=0.0,
   decision_function_shape='ovr', degree=3, gamma=2, kernel='poly',
   max_iter=-1, probability=False, random_state=None, shrinking=True,
   tol=0.001, verbose=False), <function __main__.transform_scaled>)